In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from livelossplot import PlotLossesKeras
from tensorflow import keras
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Dropout, Activation, Flatten
from keras.utils import np_utils
import warnings
warnings.filterwarnings('ignore')

In [2]:
# set random seed globally
my_seed = 21
from numpy.random import seed
seed(my_seed)
import tensorflow as tf
tf.random.set_seed(my_seed) 
# tensorflow version
print(tf.__version__)

2.6.0


MAGIC Gamma Telescope Data Set

In [3]:
# Import dataframe from https://archive.ics.uci.edu/ml/datasets/magic+gamma+telescope

df = pd.read_csv('https://archive.ics.uci.edu/ml/machine-learning-databases/magic/magic04.data',
                 names = ['fLength','fWidth','fSize','fConc','fConc1','fAsym','fM3Long','fM3Trans','fAlpha','fDist','class'])
df

fLength    fWidth   fSize   fConc  fConc1     fAsym   fM3Long  \
0       28.7967   16.0021  2.6449  0.3918  0.1982   27.7004   22.0110   
1       31.6036   11.7235  2.5185  0.5303  0.3773   26.2722   23.8238   
2      162.0520  136.0310  4.0612  0.0374  0.0187  116.7410  -64.8580   
3       23.8172    9.5728  2.3385  0.6147  0.3922   27.2107   -6.4633   
4       75.1362   30.9205  3.1611  0.3168  0.1832   -5.5277   28.5525   
...         ...       ...     ...     ...     ...       ...       ...   
19015   21.3846   10.9170  2.6161  0.5857  0.3934   15.2618   11.5245   
19016   28.9452    6.7020  2.2672  0.5351  0.2784   37.0816   13.1853   
19017   75.4455   47.5305  3.4483  0.1417  0.0549   -9.3561   41.0562   
19018  120.5135   76.9018  3.9939  0.0944  0.0683    5.8043  -93.5224   
19019  187.1814   53.0014  3.2093  0.2876  0.1539 -167.3125 -168.4558   

       fM3Trans   fAlpha     fDist class  
0       -8.2027  40.0920   81.8828     g  
1       -9.9574   6.3609  205.2610     g  
2      -45.2160  76.9600  256.7880     g  
3       -7.1513  10.4490  116.7370     g  
4       21.8393   4.6480  356.4620     g  
...         ...      ...       ...   ...  
19015    2.8766   2.4229  106.8258     h  
19016   -2.9632  86.7975  247.4560     h  
19017   -9.4662  30.2987  256.5166     h  
19018  -63.8389  84.6874  408.3166     h  
19019   31.4755  52.7310  272.3174     h  

[19020 rows x 11 columns]

In [4]:
def buildDataSet (df, test_data_fraction):
    # encoding the target column
    le = LabelEncoder()
    label = le.fit_transform(df['class'])
    label

    encoded_df = df.copy()
    encoded_df.drop("class", axis=1, inplace=True)
    encoded_df["class"] = label

    # Set the total number of classes
    nb_classes = len(encoded_df['class'].unique())

    # Creating target and features
    X = encoded_df.drop(['class'], axis=1)
    y = encoded_df['class']

    # scale the variables
    sc = StandardScaler() 
    X_scaled = sc.fit_transform(X)

    # Split into train and test set and normalize data
    X_train, X_test, y_train, y_test = train_test_split(X_scaled,y, test_size = test_data_fraction,stratify=y) #, random_state = 0)


    return encoded_df, nb_classes, X_train, X_test, y_train, y_test


class CustomWeight(tf.keras.initializers.Initializer):
    def __init__(self):
        print('gg')
    def constant_weight(self,num):
        return tf.keras.initializers.Constant(num)
    
    def normal_weight(self,mean,stddev):
        return tf.keras.initializers.RandomNormal(mean=0., stddev=1.)


def buildSequentialModel(hidden_layers_activation, first_layer_node_count, dropout_fraction, nb_classes,weight_class, wt_mean, wt_std, bias_mean, bias_std):
    # Build a Sequential Model.
    model = Sequential()
    # model.add(Flatten(input_shape=(28, 28)))
    
    model.add(Dense(first_layer_node_count, kernel_initializer=weight_class.normal_weight(wt_mean,wt_std), activation=hidden_layers_activation,bias_initializer=weight_class.normal_weight(bias_mean,bias_std)))
    model.add(Dropout(dropout_fraction))
    model.add(Dense(first_layer_node_count*0.8, kernel_initializer=weight_class.normal_weight(wt_mean,wt_std), activation=hidden_layers_activation,bias_initializer=weight_class.normal_weight(bias_mean,bias_std)))
    model.add(Dropout(dropout_fraction))
    model.add(Dense(first_layer_node_count*0.6, kernel_initializer=weight_class.normal_weight(wt_mean,wt_std), activation=hidden_layers_activation,bias_initializer=weight_class.normal_weight(bias_mean,bias_std)))
    model.add(Dropout(dropout_fraction))
    
    # Output Layer
    model.add(Dense(nb_classes, activation=hidden_layers_activation, kernel_initializer=weight_class.normal_weight(wt_mean,wt_std), bias_initializer=weight_class.normal_weight(bias_mean,bias_std)))
   
   
    return model


''' def reset_weights(model):
    for layer in model.layers:
        if isinstance(layer, tf.keras.Model): #if you're using a model as a layer
            reset_weights(layer) #apply function recursively
            continue

        #where are the initializers?
        if hasattr(layer, 'cell'):
            init_container = layer.cell
        else:
            init_container = layer

        for key, initializer in init_container.__dict__.items():
            if "initializer" not in key: #is this item an initializer?
                  continue #if no, skip it

            # find the corresponding variable, like the kernel or the bias
            if key == 'recurrent_initializer': #special case check
                var = getattr(init_container, 'recurrent_kernel')
            else:
                var = getattr(init_container, key.replace("_initializer", ""))

            var.assign(initializer(var.shape, var.dtype))
            #use the initializer '''


def Study_Activation_Functions(hidden_layers_activation, first_layer_node_count, dropout_fraction, classes, X_train, X_test, y_train, y_test,weight_class, wt_mean, wt_std, bias_mean, bias_std):
    
    # instantiate model
    model = buildSequentialModel(hidden_layers_activation, first_layer_node_count, dropout_fraction, classes,weight_class,  wt_mean, wt_std, bias_mean, bias_std)
    # compile model
    #model.compile(loss='categorical_crossentropy', optimizer='adam')
    model.compile(optimizer=keras.optimizers.Adam(learning_rate=0.001), loss=keras.losses.SparseCategoricalCrossentropy(), metrics=['accuracy'])

    model.fit(X_train, y_train, batch_size=100, epochs=600, verbose=1, validation_data=(X_test, y_test))

    train_score = model.evaluate(X_train, y_train, verbose=0)[1]
    test_score = model.evaluate(X_test, y_test, verbose=0)[1] 

    predicted_classes = np.argmax(model.predict(X_test), axis=-1)
    correct_indices = np.nonzero(predicted_classes == y_test.values)[0]
    incorrect_indices = np.nonzero(predicted_classes != y_test.values)[0]

    return train_score, test_score

In [5]:
# build dataset on our dataframe
encoded_dataframe, classes, Train_FEATURE_matrix, Test_FEATURE_matrix, Train_TARGET_matrix, Test_TARGET_matrix = buildDataSet (df, 0.2)

print(f"shape of dataframe = {encoded_dataframe.shape}")
print(f"classes in dataset = {classes}")
print(f"X_train.shape = {Train_FEATURE_matrix.shape}")
print(f"X_test.shape = {Test_FEATURE_matrix.shape}")
print(f"y_train.shape = {Train_TARGET_matrix.shape}")
print(f"y_test.shape = {Test_TARGET_matrix.shape}")
print("")
print("encoded_dataframe shown below:")
encoded_dataframe

shape of dataframe = (19020, 11)
classes in dataset = 2
X_train.shape = (15216, 10)
X_test.shape = (3804, 10)
y_train.shape = (15216,)
y_test.shape = (3804,)

encoded_dataframe shown below:


fLength    fWidth   fSize   fConc  fConc1     fAsym   fM3Long  \
0       28.7967   16.0021  2.6449  0.3918  0.1982   27.7004   22.0110   
1       31.6036   11.7235  2.5185  0.5303  0.3773   26.2722   23.8238   
2      162.0520  136.0310  4.0612  0.0374  0.0187  116.7410  -64.8580   
3       23.8172    9.5728  2.3385  0.6147  0.3922   27.2107   -6.4633   
4       75.1362   30.9205  3.1611  0.3168  0.1832   -5.5277   28.5525   
...         ...       ...     ...     ...     ...       ...       ...   
19015   21.3846   10.9170  2.6161  0.5857  0.3934   15.2618   11.5245   
19016   28.9452    6.7020  2.2672  0.5351  0.2784   37.0816   13.1853   
19017   75.4455   47.5305  3.4483  0.1417  0.0549   -9.3561   41.0562   
19018  120.5135   76.9018  3.9939  0.0944  0.0683    5.8043  -93.5224   
19019  187.1814   53.0014  3.2093  0.2876  0.1539 -167.3125 -168.4558   

       fM3Trans   fAlpha     fDist  class  
0       -8.2027  40.0920   81.8828      0  
1       -9.9574   6.3609  205.2610      0  
2      -45.2160  76.9600  256.7880      0  
3       -7.1513  10.4490  116.7370      0  
4       21.8393   4.6480  356.4620      0  
...         ...      ...       ...    ...  
19015    2.8766   2.4229  106.8258      1  
19016   -2.9632  86.7975  247.4560      1  
19017   -9.4662  30.2987  256.5166      1  
19018  -63.8389  84.6874  408.3166      1  
19019   31.4755  52.7310  272.3174      1  

[19020 rows x 11 columns]

Conventional Activation Functions to test

- Logistic regression hypothesis (Sigmoid)
- Hyperbolic Tangent (tanh) # rescaled sigmoid to (-1, +1)
- Rectified Linear Unit (ReLU)
- Gaussian Error Linear Unit (GELU) # smoothed ReLU
- Normalized Exponential Function (Softmax)

In [6]:
iterations = 10 # number of iterations that we plan to perform for each pair of hidden_layer_af - output_layer_af
dataframes = [pd.DataFrame() for _ in range(0, iterations)] # declare a list of empty dataframes to store the results of the iterations

for df_index in range(0, iterations):
    dataframes[df_index] = pd.DataFrame(columns = ['data_Dimension', 'Classes', 'Hidden_AF', 'TrainTest_Split', 'First_Hidden_Layer_Tensor_Count', 'Dropouts', 'Train_Accuracy', 'Test_Accuracy'])

# results_df = pd.DataFrame(columns = ['data_Dimension', 'Classes', 'Hidden_AF', 'Output_AF', 'TrainTest_Split', 'First_Hidden_Layer_Tensor_Count', 'Dropouts', 'Train_Accuracy', 'Test_Accuracy'])

Hidden_AF_list = ['relu', 'gelu', 'selu', 'sigmoid', 'tanh', 'softmax']
# Output_AF_list = ['gelu', 'sigmoid']
First_Hidden_Layer_Tensor_Count = 100
TrainTest_Split = 0.25
Dropouts = 0.3
wt_mean=0
wt_std=0.5
bias_mean=0
bias_std=0.25

for df_index in range(0, iterations):
    i = 0
    for haf in range(0,len(Hidden_AF_list)):
        encoded_dataframe, classes, Train_FEATURE_matrix, Test_FEATURE_matrix, Train_TARGET_matrix, Test_TARGET_matrix = buildDataSet (df, TrainTest_Split)
        train_accuracy_score, test_accuracy_score = Study_Activation_Functions(Hidden_AF_list[haf], First_Hidden_Layer_Tensor_Count, Dropouts, classes, Train_FEATURE_matrix, Test_FEATURE_matrix, Train_TARGET_matrix, Test_TARGET_matrix,CustomWeight(), wt_mean, wt_std, bias_mean, bias_std)
        dataframes[df_index].loc[i] = [encoded_dataframe.shape, classes, Hidden_AF_list[haf], TrainTest_Split, First_Hidden_Layer_Tensor_Count, Dropouts, np.round(train_accuracy_score,3), np.round(test_accuracy_score,3)]
        i = i + 1
    # model_.reset_states()
    # reset_weights(model_)    
     
    # print(f"dataframe {df_index + 1}:")
    # print(dataframes[df_index])
    # print("")

gg
Epoch 1/600
143/143 [==============================] - 3s 12ms/step - loss: 4.1639 - accuracy: 0.5889 - val_loss: 4.5152 - val_accuracy: 0.6376
Epoch 2/600
143/143 [==============================] - 0s 3ms/step - loss: 4.0542 - accuracy: 0.5999 - val_loss: 4.1868 - val_accuracy: 0.6374
Epoch 3/600
143/143 [==============================] - 2s 15ms/step - loss: 4.0471 - accuracy: 0.6114 - val_loss: 3.7544 - val_accuracy: 0.6458
Epoch 4/600
143/143 [==============================] - 1s 4ms/step - loss: 3.9676 - accuracy: 0.6076 - val_loss: 3.1584 - val_accuracy: 0.6593
Epoch 5/600
143/143 [==============================] - 2s 16ms/step - loss: 3.8635 - accuracy: 0.6147 - val_loss: 2.5519 - val_accuracy: 0.6610
Epoch 6/600
143/143 [==============================] - 1s 4ms/step - loss: 3.5245 - accuracy: 0.6196 - val_loss: 1.4027 - val_accuracy: 0.6593
Epoch 7/600
143/143 [==============================] - 2s 15ms/step - loss: 3.3913 - accuracy: 0.6214 - val_loss: 1.3046 - val_accuracy:

Epoch 58/600
143/143 [==============================] - 0s 3ms/step - loss: 1.0179 - accuracy: 0.6457 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 59/600
143/143 [==============================] - 2s 16ms/step - loss: 1.0265 - accuracy: 0.6451 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 60/600
143/143 [==============================] - 0s 3ms/step - loss: 0.9537 - accuracy: 0.6467 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 61/600
143/143 [==============================] - 2s 17ms/step - loss: 0.9546 - accuracy: 0.6458 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 62/600
143/143 [==============================] - 0s 3ms/step - loss: 0.9697 - accuracy: 0.6470 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 63/600
143/143 [==============================] - 0s 3ms/step - loss: 0.9560 - accuracy: 0.6464 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 64/600
143/143 [==============================] - 2s 15ms/step - loss: 0.9011 - accuracy: 0.6470 - val_loss: 0.6931 - val_accura

143/143 [==============================] - 0s 3ms/step - loss: 0.7191 - accuracy: 0.6484 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 115/600
143/143 [==============================] - 2s 16ms/step - loss: 0.7155 - accuracy: 0.6489 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 116/600
143/143 [==============================] - 0s 3ms/step - loss: 0.7091 - accuracy: 0.6489 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 117/600
143/143 [==============================] - 0s 3ms/step - loss: 0.7221 - accuracy: 0.6484 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 118/600
143/143 [==============================] - 2s 17ms/step - loss: 0.7068 - accuracy: 0.6490 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 119/600
143/143 [==============================] - 0s 3ms/step - loss: 0.7169 - accuracy: 0.6482 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 120/600
143/143 [==============================] - 2s 16ms/step - loss: 0.7131 - accuracy: 0.6491 - val_loss: 0.6931 - val_accuracy: 0.6

143/143 [==============================] - 0s 3ms/step - loss: 0.7034 - accuracy: 0.6486 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 171/600
143/143 [==============================] - 2s 15ms/step - loss: 0.7011 - accuracy: 0.6488 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 172/600
143/143 [==============================] - 0s 3ms/step - loss: 0.7052 - accuracy: 0.6485 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 173/600
143/143 [==============================] - 2s 16ms/step - loss: 0.6999 - accuracy: 0.6489 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 174/600
143/143 [==============================] - 0s 3ms/step - loss: 0.7003 - accuracy: 0.6482 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 175/600
143/143 [==============================] - 0s 3ms/step - loss: 0.7047 - accuracy: 0.6479 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 176/600
143/143 [==============================] - 2s 16ms/step - loss: 0.7067 - accuracy: 0.6479 - val_loss: 0.6931 - val_accuracy: 0.6

143/143 [==============================] - 2s 16ms/step - loss: 0.6992 - accuracy: 0.6484 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 227/600
143/143 [==============================] - 0s 3ms/step - loss: 0.7012 - accuracy: 0.6484 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 228/600
143/143 [==============================] - 2s 16ms/step - loss: 0.7000 - accuracy: 0.6488 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 229/600
143/143 [==============================] - 0s 3ms/step - loss: 0.7034 - accuracy: 0.6484 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 230/600
143/143 [==============================] - 0s 3ms/step - loss: 0.7075 - accuracy: 0.6482 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 231/600
143/143 [==============================] - 2s 16ms/step - loss: 0.7010 - accuracy: 0.6487 - val_loss: 0.6931 - val_accuracy: 0.6484
Epoch 232/600
143/143 [==============================] - 0s 3ms/step - loss: 0.7034 - accuracy: 0.6484 - val_loss: 0.6931 - val_accuracy: 0.6

...

143/143 [==============================] - 2s 17ms/step - loss: 0.2899 - accuracy: 0.8803 - val_loss: 0.3184 - val_accuracy: 0.8713
Epoch 357/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2888 - accuracy: 0.8811 - val_loss: 0.3187 - val_accuracy: 0.8711
Epoch 358/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2911 - accuracy: 0.8801 - val_loss: 0.3182 - val_accuracy: 0.8709
Epoch 359/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2919 - accuracy: 0.8780 - val_loss: 0.3182 - val_accuracy: 0.8721
Epoch 360/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2887 - accuracy: 0.8824 - val_loss: 0.3184 - val_accuracy: 0.8713
Epoch 361/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2880 - accuracy: 0.8819 - val_loss: 0.3188 - val_accuracy: 0.8715
Epoch 362/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2884 - accuracy: 0.8820 - val_loss: 0.3185 - val_accuracy: 0.8

143/143 [==============================] - 2s 17ms/step - loss: 0.2852 - accuracy: 0.8812 - val_loss: 0.3192 - val_accuracy: 0.8705
Epoch 413/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2854 - accuracy: 0.8823 - val_loss: 0.3196 - val_accuracy: 0.8715
Epoch 414/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2867 - accuracy: 0.8823 - val_loss: 0.3188 - val_accuracy: 0.8698
Epoch 415/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2832 - accuracy: 0.8841 - val_loss: 0.3195 - val_accuracy: 0.8715
Epoch 416/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2878 - accuracy: 0.8812 - val_loss: 0.3194 - val_accuracy: 0.8713
Epoch 417/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2845 - accuracy: 0.8820 - val_loss: 0.3191 - val_accuracy: 0.8713
Epoch 418/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2847 - accuracy: 0.8833 - val_loss: 0.3192 - val_accuracy: 0.8

143/143 [==============================] - 2s 17ms/step - loss: 0.2857 - accuracy: 0.8826 - val_loss: 0.3196 - val_accuracy: 0.8707
Epoch 469/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2817 - accuracy: 0.8850 - val_loss: 0.3199 - val_accuracy: 0.8715
Epoch 470/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2852 - accuracy: 0.8841 - val_loss: 0.3194 - val_accuracy: 0.8715
Epoch 471/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2849 - accuracy: 0.8821 - val_loss: 0.3192 - val_accuracy: 0.8717
Epoch 472/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2848 - accuracy: 0.8832 - val_loss: 0.3196 - val_accuracy: 0.8707
Epoch 473/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2842 - accuracy: 0.8824 - val_loss: 0.3200 - val_accuracy: 0.8721
Epoch 474/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2856 - accuracy: 0.8824 - val_loss: 0.3199 - val_accuracy: 0.8

143/143 [==============================] - 0s 3ms/step - loss: 0.2833 - accuracy: 0.8815 - val_loss: 0.3187 - val_accuracy: 0.8713
Epoch 525/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2818 - accuracy: 0.8830 - val_loss: 0.3201 - val_accuracy: 0.8709
Epoch 526/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2806 - accuracy: 0.8836 - val_loss: 0.3198 - val_accuracy: 0.8721
Epoch 527/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2817 - accuracy: 0.8829 - val_loss: 0.3201 - val_accuracy: 0.8713
Epoch 528/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2839 - accuracy: 0.8831 - val_loss: 0.3196 - val_accuracy: 0.8713
Epoch 529/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2831 - accuracy: 0.8825 - val_loss: 0.3199 - val_accuracy: 0.8713
Epoch 530/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2800 - accuracy: 0.8843 - val_loss: 0.3196 - val_accuracy: 0.8

143/143 [==============================] - 0s 3ms/step - loss: 0.2791 - accuracy: 0.8845 - val_loss: 0.3210 - val_accuracy: 0.8726
Epoch 581/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2802 - accuracy: 0.8839 - val_loss: 0.3206 - val_accuracy: 0.8723
Epoch 582/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2790 - accuracy: 0.8838 - val_loss: 0.3207 - val_accuracy: 0.8728
Epoch 583/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2791 - accuracy: 0.8839 - val_loss: 0.3210 - val_accuracy: 0.8732
Epoch 584/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2781 - accuracy: 0.8825 - val_loss: 0.3213 - val_accuracy: 0.8726
Epoch 585/600
143/143 [==============================] - 0s 3ms/step - loss: 0.2760 - accuracy: 0.8850 - val_loss: 0.3216 - val_accuracy: 0.8717
Epoch 586/600
143/143 [==============================] - 2s 17ms/step - loss: 0.2815 - accuracy: 0.8822 - val_loss: 0.3204 - val_accuracy: 0.8

In [7]:
results_df = dataframes[0]
results_df = results_df.rename(columns={"Train_Accuracy": "Robust_Train_Accuracy", "Test_Accuracy": "Robust_Test_Accuracy"})
for df_index in range(1, iterations):
    results_df['Robust_Train_Accuracy'] = results_df['Robust_Train_Accuracy'] + dataframes[df_index]['Train_Accuracy']
    results_df['Robust_Test_Accuracy'] = results_df['Robust_Test_Accuracy'] + dataframes[df_index]['Test_Accuracy']
results_df['Robust_Train_Accuracy'] = round((results_df['Robust_Train_Accuracy'] / iterations),4)
results_df['Robust_Test_Accuracy'] = round((results_df['Robust_Test_Accuracy'] / iterations),4)

results_df.to_csv("results_df.csv")
results_df.sort_values(by = 'Robust_Test_Accuracy', ascending=False)

data_Dimension  Classes Hidden_AF  TrainTest_Split  \
3    (19020, 11)        2   sigmoid             0.25   
5    (19020, 11)        2   softmax             0.25   
4    (19020, 11)        2      tanh             0.25   
0    (19020, 11)        2      relu             0.25   
1    (19020, 11)        2      gelu             0.25   
2    (19020, 11)        2      selu             0.25   

   First_Hidden_Layer_Tensor_Count  Dropouts  Robust_Train_Accuracy  \
3                              100       0.3                 0.8880   
5                              100       0.3                 0.8915   
4                              100       0.3                 0.6480   
0                              100       0.3                 0.6480   
1                              100       0.3                 0.6480   
2                              100       0.3                 0.6480   

   Robust_Test_Accuracy  
3                0.8752  
5                0.8745  
4                0.6481  
0                0.6480  
1                0.6480  
2                0.6480